In [1]:
import pandas as pd
import json

In [2]:
# Record 4289223 is most of our initial 404s (ultimately just second most), 
# looks like they align with 0.2.rachel.blow.mel.tim.ikiam.csv, so we'll check
fof_df = pd.read_csv("../metadata/deduplication/Zenodo_meta_files/0.2.rachel.blow.mel.tim.ikiam.csv", low_memory = False)
fof_df.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50 entries, 0 to 49
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   File name   50 non-null     object
 1   ID          49 non-null     object
 2   Side        49 non-null     object
 3   Unnamed: 3  49 non-null     object
dtypes: object(4)
memory usage: 1.7+ KB


In [3]:
fof_df.head()

File name         ID     Side Unnamed: 3
0  CAM028501d.JPG  CAM028501   dorsal      d.JPG
1  CAM028501v.JPG  CAM028501  ventral      v.JPG
2  CAM028502d.JPG  CAM028502   dorsal      d.JPG
3  CAM028502v.JPG  CAM028502  ventral      v.JPG
4  CAM028503d.JPG  CAM028503   dorsal      d.JPG

These don't have a URL, but it could be reconstructed from the record number. Let's check if these are the files that had the 404 error from that record.

In [4]:
ERROR_PATH = "../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_error_log_(readable).json"
with open(ERROR_PATH, "r") as error_file:
    errors = json.loads(error_file.read())

error_df = pd.DataFrame(data = errors)
error_df.head()

Image  \
0  Heliconius melpomene ssp. plesseni x malleti/5...   
1  Heliconius erato ssp. notabilis x lativitta/54...   
2  Heliconius erato ssp. notabilis x lativitta/55...   
3  Heliconius melpomene ssp. plesseni x malleti/1...   
4  Heliconius melpomene ssp. plesseni x malleti/1...   

                                            file_url record_number  \
0  https://zenodo.org/record/3082688/files/CAM017...       3082688   
1  https://zenodo.org/record/3082688/files/CAM017...       3082688   
2  https://zenodo.org/record/3082688/files/CAM017...       3082688   
3  https://zenodo.org/record/1748277/files/CAM017...       1748277   
4  https://zenodo.org/record/1748277/files/CAM017...       1748277   

            dataset      CAMID Response_status  
0  Patricio Salazar  CAM017505             404  
1  Patricio Salazar  CAM017693             404  
2  Patricio Salazar  CAM017821             404  
3  Patricio Salazar  CAM017932             404  
4  Patricio Salazar  CAM017971             404

In [5]:
rec_4289223_df = error_df.loc[error_df["record_number"] == "4289223"]

missing_camids = []
for camid in list(rec_4289223_df["CAMID"].unique()):
    if camid not in list(fof_df.ID):
        missing_camids.append(camid)

print(rec_4289223_df.CAMID.nunique())
print(len(missing_camids))

23
0


Looks like they're all captured in this CSV, so we can check their URLs?

In [6]:
list(rec_4289223_df.file_url.sample(7))

['https://zenodo.org/record/4289223/files/CAM028509v.JPG',
 'https://zenodo.org/record/4289223/files/CAM028504d.JPG',
 'https://zenodo.org/record/4289223/files/CAM028508v.JPG',
 'https://zenodo.org/record/4289223/files/CAM028509d.JPG',
 'https://zenodo.org/record/4289223/files/CAM028502v.JPG',
 'https://zenodo.org/record/4289223/files/CAM028513v.CR2',
 'https://zenodo.org/record/4289223/files/CAM028514d.JPG']

These are listed in the CSV, but do not show up on the [record page](https://zenodo.org/records/4289223).

We saw in `EDA-DL-0-1.ipynb` that none of the error images were in the multimedia file from record 3477891, so we don't have a clear patch. All error records were saved to a CSV through that notebook.

In [7]:
error_df = pd.read_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_error_log.csv", low_memory = False)
print(error_df.columns)

master = pd.read_csv("../metadata/Jiggins_Zenodo_Img_Master_3477891Patch.csv", low_memory = False)

Index(['Image', 'file_url', 'record_number', 'dataset', 'CAMID',
       'Response_status', 'filename', 'view'],
      dtype='object')


In [8]:
error_42 = error_df.loc[error_df["record_number"] == 4289223].copy()
error_42.head()

Image  \
5  Heliconius melpomene ssp. malleti/14972_CAM028...   
6  Heliconius melpomene ssp. malleti/14971_CAM028...   
7  Heliconius melpomene ssp. malleti/14973_CAM028...   
8  Heliconius melpomene ssp. malleti/14974_CAM028...   
9  Heliconius melpomene ssp. plesseni/14975_CAM02...   

                                            file_url  record_number  \
5  https://zenodo.org/record/4289223/files/CAM028...        4289223   
6  https://zenodo.org/record/4289223/files/CAM028...        4289223   
7  https://zenodo.org/record/4289223/files/CAM028...        4289223   
8  https://zenodo.org/record/4289223/files/CAM028...        4289223   
9  https://zenodo.org/record/4289223/files/CAM028...        4289223   

                dataset      CAMID  Response_status              filename  \
5  Cambridge Collection  CAM028501              404  14972_CAM028501v.JPG   
6  Cambridge Collection  CAM028501              404  14971_CAM028501d.JPG   
7  Cambridge Collection  CAM028502              404  14973_CAM028502d.JPG   
8  Cambridge Collection  CAM028502              404  14974_CAM028502v.JPG   
9  Cambridge Collection  CAM028503              404  14975_CAM028503d.JPG   

      view  
5  ventral  
6   dorsal  
7   dorsal  
8  ventral  
9   dorsal

In [9]:
def get_x(filename):
    return int(filename.split("_")[0])

In [10]:
error_42["X"] = error_42["filename"].apply(get_x)

master_42 = master.loc[master["X"].isin(list(error_42["X"]))].copy()
master_42.head()

CAMID      X      Image_name     View  \
24194  CAM028501  14972  CAM028501v.JPG  ventral   
24195  CAM028501  14971  CAM028501d.JPG   dorsal   
24196  CAM028502  14973  CAM028502d.JPG   dorsal   
24197  CAM028502  14974  CAM028502v.JPG  ventral   
24198  CAM028503  14975  CAM028503d.JPG   dorsal   

                             zenodo_name                        zenodo_link  \
24194  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24195  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24196  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24197  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24198  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   

      Sequence                      Taxonomic_Name    Locality  \
24194   28,501   Heliconius melpomene ssp. malleti  Río Pusuno   
24195   28,501   Heliconius melpomene ssp. malleti  Río Pusuno   
24196   28,502   Heliconius melpomene ssp. malleti  Río Pusuno   
24197   28,502   Heliconius melpomene ssp. malleti  Río Pusuno   
24198   28,503  Heliconius melpomene ssp. plesseni  Huaymayaco   

      Sample_accession  ... Stage   Sex Unit_Type file_type record_number  \
24194              NaN  ...   NaN  Male      Wild       jpg       4289223   
24195              NaN  ...   NaN  Male      Wild       jpg       4289223   
24196              NaN  ...   NaN  Male      Wild       jpg       4289223   
24197              NaN  ...   NaN  Male      Wild       jpg       4289223   
24198              NaN  ...   NaN  Male      Wild       jpg       4289223   

                    species subspecies       genus  \
24194  Heliconius melpomene    malleti  Heliconius   
24195  Heliconius melpomene    malleti  Heliconius   
24196  Heliconius melpomene    malleti  Heliconius   
24197  Heliconius melpomene    malleti  Heliconius   
24198  Heliconius melpomene   plesseni  Heliconius   

                                                file_url hybrid_stat  
24194  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  
24195  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  
24196  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  
24197  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  
24198  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  

[5 rows x 28 columns]

In [11]:
master.loc[(master["Image_name"].isin(list(master_42.Image_name.unique()))) & (~master["record_number"] == 4289223)]

Empty DataFrame
Columns: [CAMID, X, Image_name, View, zenodo_name, zenodo_link, Sequence, Taxonomic_Name, Locality, Sample_accession, Collected_by, Other_ID, Date, Dataset, Store, Brood, Death_Date, Cross_Type, Stage, Sex, Unit_Type, file_type, record_number, species, subspecies, genus, file_url, hybrid_stat]
Index: []

[0 rows x 28 columns]

Can't align these elsewhere based on `Image_name` either.